In [25]:
import pandas as pd
import plotly.graph_objects as go

In [26]:
# --- USER SETTINGS ---
h_out_default = 5.0  # W/m²·K

## Run insulation model on 2021 weather data

In [27]:
weather_df = pd.read_csv("data-collection/weather_2021.csv")
weather_df["timestamp"] = pd.to_datetime(weather_df["timestamp"])
weather_df.set_index("timestamp", inplace=True)

In [47]:
# --- 1. Read box configurations ---
df_cfg = pd.read_csv("data-collection/box_insulated_thermal_time_constants.csv")
df_cfg["C_total (J/K)"] = df_cfg["C_total (J/K)"].astype(float)
df_cfg["R_total (K/W)"] = df_cfg["R_total (K/W)"].astype(float)

# --- 2. Simulation function ---
def simulate_box(T_out_series, C, R_total, dt=3600):
    T = T_out_series.iloc[0]
    res = []
    for T_out in T_out_series:
        T = T + (dt / (C * R_total)) * (T_out - T)
        res.append(T)
    return pd.Series(res, index=T_out_series.index)  # keep datetime index

# --- 3. Create Plotly figure ---
fig = go.Figure()

# Outdoor temperature
fig.add_trace(go.Scatter(
    x=weather_df.index,
    y=weather_df["T_out"],
    mode="lines",
    name="Outdoor Temp",
    opacity=0.5,
    line=dict(color='gray')
))

# Simulate each box configuration
for _, row in df_cfg.iterrows():
    C = row["C_total (J/K)"]
    R = row["R_total (K/W)"]
    series = simulate_box(weather_df["T_out"], C, R)
    series = series.astype(float).ffill()  # forward-fill missing values
    label = f"{int(row.get('insulation (mm)',0))} mm, {row.get('water (L)',0)} L, h={row.get('h_out (W/m2K)', h_out_default)}"
    
    fig.add_trace(go.Scatter(
        x=series.index,
        y=series.values,
        mode='lines',
        name=label,
        opacity=1,
        connectgaps=False,
        visible=True if row.get('water (L)')==5.0 else 'legendonly'
    ))

# Layout
fig.update_layout(
    title="Box Temperature Simulations (2021 Outdoor Temps)",
    xaxis_title="Date",
    yaxis_title="Temperature (°C)",
    xaxis=dict(
        showgrid=True,
        tickformat="%b %d",  # Month Day format
        nticks=12
    ),
    legend=dict(title="Box Configurations"),
    template="plotly_white",
    width=1200,
    height=600
)

fig.show()


## Adding warm water bottle

In [45]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go

# --- Box and environment parameters ---
C_soil = 8000      # J/K (10 kg soil)
C_water = 20930    # J/K (5 L water)
C_total = C_soil + C_water

T_out = -5         # °C
T_initial_list = [20, 50]  # initial water temperatures
insulation_mm_list = [50, 100, 200, 500]
R_50mm = 1.2       # K/W for 50mm wool
dt = 3600          # 1 hour timestep
hours_total = 24*7 # simulate one week

# --- Simulation ---
time_hours = np.arange(0, hours_total + 1)
fig = go.Figure()

for T_init in T_initial_list:
    for R_mm in insulation_mm_list:
        # Scale thermal resistance linearly with thickness
        R_total = R_50mm * (R_mm / 50)
        
        # Initialize temperature array
        T = np.zeros_like(time_hours, dtype=float)
        T[0] = T_init
        
        # Compute tau
        tau = C_total * R_total
        
        # Simulation loop
        for i in range(1, len(time_hours)):
            T[i] = T[i-1] + (dt / tau) * (T_out - T[i-1])
        
        # Add to Plotly figure
        fig.add_trace(go.Scatter(
            x=time_hours,
            y=T,
            mode='lines',
            name=f"{R_mm}mm wool, T_init={T_init}°C",
            visible='legendonly' if T_init==50 else True  # 20°C lines visible, 50°C hidden
        ))

# Layout
fig.update_layout(
    title="Temperature decay of bin with different insulation and water temps",
    xaxis_title="Time (hours)",
    yaxis_title="Bin Temperature (°C)",
    template="plotly_white",
    width=1000,
    height=600
)

fig.show()
